<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:80px;" src="https://hpp.education/Lessons/docet.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>

<center>
<h3 style="color:#888888;"> <i>--  AER004: Mécanique des fluides appliquée  --</i> </h3>
<h1> TN n°6 </h1>
<h3> Calcul de la poussée moteur </h3>
<h6><a href="mailto:simon.marie@lecnam.net">simon.marie@lecnam.net</a></h6>
</center>




Pour ceux qui ne seraient pas familier avec le language python, vous pouvez consulter le Notebook <a href="https://hpp.education/Lessons/Python/Intro_python.html">Introduction au Python</a>. 

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib
matplotlib.style.use('fivethirtyeight')
%matplotlib inline

L'objectif de ce TN est de se familiariser avec les relations isentropiques pour le calcul de la poussé d'un moteur fusée.
En effet, la poussée d'un moteur fusée est basée sur le principe d'ejection de gaz à grande vitesse en sortie de tuyère. La formule de la poussée est donnée par:

$$
F=\left[ (p_e-p_a)+\rho_e U_e^2\right] S_e 
$$

Ici $p_a$ représente la pression atmosphérique, et les indices $_e$ sont relatifs aux grandeurs en sortie de tuyère.

La poussée d'un moteur fusée est généralement obtenue par combustion d'un carburant (ex: Hydrogène) et d'un comburant (ex: oxygène) qui réagissent à très grande température et à très grande pression. Ces propriétés initiales de la combustion sont appelées *conditions génératrices* et dépendent du couple carburant/comburant choisi. On les notes généralement avec un indice $_i$ ($T_i$: Température génératrices, $p_i$: pression génératrice). La tuyère est alors utilisé comme dispositif pour optimiser la détente des gaz issues de la combustion et augmenter leur vitesse d'éjection. On considérera ici que cette détente est isentropique pour pouvoir utiliser les relations vues en cours.

En se plaçant dans le vide, ($p_a=0$) on peut exprimer la poussée en fonction des conditions génératrices $p_i$ et $T_i$:

$$
F=p_e\left[ 1+\gamma M_e^2\right] S_e = p_i \dfrac{p_e}{p_i} \left[ 1+\gamma M_e^2\right] S_c \dfrac{S_e}{S_c}
$$

On fait donc apparaitre la relation isentropique de la pression $\dfrac{p_e}{p_i}$ et la loi des sections $\dfrac{S_e}{S_c}$. Soit:

$$
\dfrac{p_e}{p_i}=\left(1+\dfrac{\gamma-1}{2}M_e^2 \right)^{-\gamma/(\gamma-1)}
$$

et

$$
\dfrac{S_e}{S_c}=\dfrac{1}{M_e}\left(\dfrac{2}{\gamma+1}\right)^{\frac{\gamma+1}{2(\gamma-1)}}\left(1+\dfrac{\gamma-1}{2}M_e^2\right)^{\frac{\gamma+1}{2(\gamma-1)}}
$$

On remarque donc que l'on peut écrire la poussée sous la forme:

$$
F=\Phi(R_s,\gamma) p_i S_c
$$

Ou $\Phi$ est une fonction ne dépendant que du $\gamma$ et du rapport des sections $R_s=\dfrac{S_e}{S_c}$.

# Calcul du nombre de Mach en sortie $M_e$

Pour calculer $M_e$ en connaissant $R_s$, il faut inverser la loi des sections. On peut le faire numériquement avec la fonction suivante:

In [ ]:
def section( Rs,g ):
	M=1
	S=1
	while (abs(S-Rs)>1e-2):
		S=(1./M)*((2./(g+1.))+((g-1.)/(g+1.))*M**2)**((g+1.)/(2.*(g-1.)))
		M+=0.0005
	M0=M
	return M0

In [ ]:
section(10,1.4)

In [ ]:
section(10,1.27)

# Calcul de la fonction $\Phi$

On peut maintenant calculer la fonction $\Phi(R_s,\gamma)$

In [ ]:
def Fpoussee(Rs,g):
    '''
    Calcul de la fonction de poussée en fonction du gamma et du rapport de section r
    '''
    Me=section( Rs,g )
    pepi=(1+((g-1)/2.)*Me**2)**-(g/(g-1))
    phi=pepi*Rs*(1+g*Me**2)
    return phi



# Calcul du débit de tuyère

Le débit massique est supposé constant dans la tuyère. On peut donc l'exprimer au niveau du col ou le nombre de Mach vaut 1 ($U_c=c_c$):

$$
q_m=\rho_c S_c U_c=\dfrac{\rho_c}{\rho_i}\dfrac{c_c}{c_i}\rho_i c_i S_c=\dfrac{\rho_c}{\rho_i}\dfrac{c_c}{c_i}\dfrac{c_i}{rT_i}p_i S_c
$$

On peut donc exprimer le débit sous la forme:

$$
q_m=\phi(\gamma,T_i)p_i S_c
$$

avec:

$$
\phi(\gamma,T_i)=\dfrac{\rho_c}{\rho_i}\dfrac{c_c}{c_i}\dfrac{\sqrt{\gamma r T_i}}{rT_i}=\left(1+\dfrac{\gamma-1}{2}\right)^{\frac{-1}{\gamma-1}}\left(1+\dfrac{\gamma-1}{2}\right)^{-1}\sqrt{\gamma}\dfrac{1}{\sqrt{rT_i}}
$$

In [ ]:
def qbar(Ti,r,g):
    G=1+0.5*(g-1)
    phi=np.sqrt(g)*G**(-g/(g-1))/np.sqrt(r*Ti)
    return phi

# Calcul de l'ISP d'un moteur

L'impulsion spécifique d'un moteur fusée est caractéristique de ses performances dans le vide. Il s'exprime sous la forme:

$$
ISP=\dfrac{F}{q_m g_0}
$$

Il exprime donc le rapport entre la force de poussée et le poid de carburant consommé par seconde pour produire cette poussée. Il s'exprime donc en seconde.

D'après les résultats précédent on peut écrire:

$$
ISP=\dfrac{\Phi(R_s,\gamma)}{g_0\phi(T_i,r,\gamma)}
$$


In [ ]:
def ISP(Rs,g,r,Ti):
    Phi=Fpoussee(Rs,g)
    phi=qbar(Ti,r,g)
    IS=Phi/phi
    return IS/9.81


In [ ]:
ISP(60,1.4,245,3500)

In [1]:
from IPython.core.display import HTML
style=open('notebooks.css', "r").read()
HTML(style)

<a id="top" style="float:left;" href="http://dynfluid.ensam.eu/"><img style="height:80px;" src="https://hpp.education/Lessons/docet.png"/></a>
<a style="float:right;" href="http://www.cnam.fr//"><img style="height:80px;" src="https://upload.wikimedia.org/wikipedia/commons/6/66/Logo_cnam.gif"/></a>